In [1]:
import glob, re, os
import numpy as np
import matplotlib.pyplot as plt
from typing import List
%run ../Task_4/cardiac_ml_tools.py

In [2]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import tensorflow as tf

from sklearn.metrics import accuracy_score, precision_score, recall_score
from sklearn.model_selection import train_test_split
from tensorflow.keras import layers, losses
from tensorflow.keras.datasets import fashion_mnist
from tensorflow.keras.models import Model

/Users/movsesyanae/miniconda3/envs/ml/lib/python3.9/site-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.25.0
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


# Reading In The Data

In [3]:
data_dirs = []
regex = r'data_hearts_dd_0p2*'
DIR='../../cardiac_challenge/intracardiac_dataset/' # This should be the path to the intracardiac_dataset, it can be downloaded using data_science_challenge_2023/download_intracardiac_dataset.sh
for x in os.listdir(DIR):
    if re.match(regex, x):
        data_dirs.append(DIR + x)
file_pairs = read_data_dirs(data_dirs)

In [4]:
num_timesteps = 500

In [5]:
all_pECG_data = np.empty(shape=(len(file_pairs), num_timesteps, 12))
all_Vm_data = np.empty(shape=(len(file_pairs), num_timesteps, 75))
for index,(pecg, vm) in enumerate(file_pairs):
    print("pecg", pecg)
    print("vm", vm)
    all_Vm_data[index] = np.load(vm)
    all_pECG_data[index] = get_standard_leads(np.load(pecg))

pecg ../../cardiac_challenge/intracardiac_dataset/data_hearts_dd_0p2_geo_act_1_bcl_gkr/pECGData_hearts_dd_0p2_geo_act_1_bcl_gkr_bcl.1000.gkr.000.pattern.0.volunteer.v12.npy
vm ../../cardiac_challenge/intracardiac_dataset/data_hearts_dd_0p2_geo_act_1_bcl_gkr/VmData_hearts_dd_0p2_geo_act_1_bcl_gkr_bcl.1000.gkr.000.pattern.0.volunteer.v12.npy
pecg ../../cardiac_challenge/intracardiac_dataset/data_hearts_dd_0p2_geo_act_1_bcl_gkr/pECGData_hearts_dd_0p2_geo_act_1_bcl_gkr_bcl.1000.gkr.000.pattern.0.volunteer.v16.npy
vm ../../cardiac_challenge/intracardiac_dataset/data_hearts_dd_0p2_geo_act_1_bcl_gkr/VmData_hearts_dd_0p2_geo_act_1_bcl_gkr_bcl.1000.gkr.000.pattern.0.volunteer.v16.npy
pecg ../../cardiac_challenge/intracardiac_dataset/data_hearts_dd_0p2_geo_act_1_bcl_gkr/pECGData_hearts_dd_0p2_geo_act_1_bcl_gkr_bcl.1000.gkr.000.pattern.0.volunteer.v2.npy
vm ../../cardiac_challenge/intracardiac_dataset/data_hearts_dd_0p2_geo_act_1_bcl_gkr/VmData_hearts_dd_0p2_geo_act_1_bcl_gkr_bcl.1000.gkr.000.pat

# Normalizing The Data

In [6]:
# Getting the range of the data
print("Maximum value in the whole array:%d"%(all_pECG_data.max()))                    
print("Maximum value in the whole array:%d"%(all_pECG_data.min()))                    
print("Maximum value in the whole array:%d"%(all_Vm_data.max()))                    
print("Maximum value in the whole array:%d"%(all_Vm_data.min()))                    

Maximum value in the whole array:5
Maximum value in the whole array:-5
Maximum value in the whole array:49
Maximum value in the whole array:-93



We can see that 
* pECG Data is between -5 and 5
* Vm Data is between -93 and 49

In [ ]:
# all_pECG_data = (all_pECG_data + 5) / 10
# all_Vm_data = (all_Vm_data + 100) / 150

# Splitting The Data

In [7]:
x_train, x_test, y_train, y_test = train_test_split(all_pECG_data, all_Vm_data, test_size = 0.20, random_state = 0)

# Defining The Model

In [8]:
from tensorflow.keras.layers import Conv1D, Input, Dense, Flatten, Lambda, Conv1DTranspose, Reshape
import tensorflow as tf
from tensorflow import keras


In [9]:
def get_model(upscale_dimension=75, channels=1):
    conv_args = {
        "activation": "relu",
        'kernel_size': 5,
        'strides': 1,
        'padding': 'same'
    }
    input_layer = keras.Input(shape=(500, 12))
    
    layer = keras.layers.Conv1D(filters=32, **conv_args)(input_layer)
    layer = keras.layers.Conv1D(filters=64, **conv_args)(layer)
    layer = keras.layers.Conv1D(filters=128, **conv_args)(layer)
    layer = keras.layers.Conv1D(filters=256, **conv_args)(layer)
    # convt = keras.layers.Conv1DTranspose(filters=75, kernel_size=1, **conv_args)(conv)
    
    output_layer = keras.layers.Dense(units=75)(layer)
    
    return keras.Model(input_layer, output_layer)
model = get_model()
display(model.summary())

2023-08-03 09:30:22.628862: I metal_plugin/src/device/metal_device.cc:1154] Metal device set to: Apple M1 Pro
2023-08-03 09:30:22.629947: I metal_plugin/src/device/metal_device.cc:296] systemMemory: 16.00 GB
2023-08-03 09:30:22.629962: I metal_plugin/src/device/metal_device.cc:313] maxCacheSize: 5.33 GB
2023-08-03 09:30:22.630256: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:303] Could not identify NUMA node of platform GPU ID 0, defaulting to 0. Your kernel may not have been built with NUMA support.
2023-08-03 09:30:22.630666: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:269] Created TensorFlow device (/job:localhost/replica:0/task:0/device:GPU:0 with 0 MB memory) -> physical PluggableDevice (device: 0, name: METAL, pci bus id: <undefined>)


Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 500, 12)]         0         
                                                                 
 conv1d (Conv1D)             (None, 500, 32)           1952      
                                                                 
 conv1d_1 (Conv1D)           (None, 500, 64)           10304     
                                                                 
 conv1d_2 (Conv1D)           (None, 500, 128)          41088     
                                                                 
 conv1d_3 (Conv1D)           (None, 500, 256)          164096    
                                                                 
 dense (Dense)               (None, 500, 75)           19275     
                                                                 
Total params: 236715 (924.67 KB)
Trainable params: 236715 (92

None

In [10]:
model = get_model()
display(model.summary())

Model: "model_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_2 (InputLayer)        [(None, 500, 12)]         0         
                                                                 
 conv1d_4 (Conv1D)           (None, 500, 32)           1952      
                                                                 
 conv1d_5 (Conv1D)           (None, 500, 64)           10304     
                                                                 
 conv1d_6 (Conv1D)           (None, 500, 128)          41088     
                                                                 
 conv1d_7 (Conv1D)           (None, 500, 256)          164096    
                                                                 
 dense_1 (Dense)             (None, 500, 75)           19275     
                                                                 
Total params: 236715 (924.67 KB)
Trainable params: 236715 (

None

In [11]:
loss_fn = keras.losses.MeanSquaredError()
optimizer = keras.optimizers.legacy.Adam(learning_rate=0.1)

In [ ]:
model.compile(optimizer='adam', loss='mae', metrics=['accuracy'])
history = model.fit(x_train, y_train, 
          epochs=150, 
          batch_size=32,
          validation_data=(x_test, y_test),
          shuffle=True)

In [ ]:
plt.plot(history.history["loss"], label="Training Loss")
plt.plot(history.history["val_loss"], label="Validation Loss")
plt.legend()

In [ ]:
sample = 45
image = x_test[sample:sample+1]
decoded_imgs = model(image).numpy()
VmData = decoded_imgs[0]
row = 7
column = 10
plt.figure(figsize=(18, 9))

print(VmData.shape[1])
for count, i in enumerate(range(VmData.shape[1])):
    plt.subplot(8, 10, count + 1)
    plt.plot(VmData[0:num_timesteps,i])
    plt.title(f'i = {i}')
    plt.grid(visible=True, which='major', color='#666666', linestyle='-')
    plt.minorticks_on()
    plt.grid(visible=True, which='minor', color='#999999', linestyle='-', alpha=0.2)
    # plt.xlabel('msec')
    # plt.ylabel('mV')
plt.tight_layout()
plt.show()
# close
plt.close()

VmData = y_test[sample]
plt.figure(figsize=(18, 9))

print(VmData.shape[1])
for count, i in enumerate(range(VmData.shape[1])):
    plt.subplot(8, 10, count + 1)
    plt.plot(VmData[0:num_timesteps,i])
    plt.title(f'i = {i}')
    plt.grid(visible=True, which='major', color='#666666', linestyle='-')
    plt.minorticks_on()
    plt.grid(visible=True, which='minor', color='#999999', linestyle='-', alpha=0.2)
    # plt.xlabel('msec')
    # plt.ylabel('mV')
plt.tight_layout()
plt.show()
# close
plt.close()

In [ ]:
model.save('t4-cnn-150.h5')

In [12]:
model = keras.models.load_model('t4-cnn-150.h5')

In [13]:
y_pred = model.predict(x_test)

2023-08-03 11:00:47.583701: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:114] Plugin optimizer for device_type GPU is enabled.


101/101 [==============================] - 2s 12ms/step


In [14]:
abs_err = np.abs(y_test - y_pred)
print('MAE:', np.mean(abs_err))
print('std:', np.std(abs_err))

MAE: 6.6856236222692
std: 16.01612056162511


In [15]:
err = y_test - y_pred
print('ME:', np.mean(err))
print('std:', np.std(err))

ME: 0.44954620586861244
std: 17.349685566947365
